# Requêtes flexibles et stratégies d’exécution
## Travail à faire et à rendre
Ce cahier (notebook) Jupyter est à la fois l'énoncé du TP et ce qu'il faudra déposer à la fin de la séance sur l’ENT. Il vous sera demandé de remplir les cellules prévues avec vos réponses qui pourront être du texte en *markdown*, voir **[ce lien](https://commonmark.org/help/)** pour la syntaxe exacte. Ça aussi pourra être des requêtes SQL dont le résultat apparaîtra en dessous, ou des scripts Python pour calculer une information plus complexe.

Rappel: taper <kbd>entrée</kbd> pour exécuter une cellule et passer à la suivante. Tapez <kbd>CTRL</kbd><kbd>entrée</kbd> pour évaluer une cellule sans passer à la suivante.

## Préparation
### Connexion au serveur PostgreSQL et accès aux données en mode shell
Vous allez commencer par installer la base de données et y insérer toutes les données du TP. C’est une base appelée `SecondHandCars`.

Voici la commande pour commencer, à ne faire qu'une seule fois en tout (de toutes les séances de TP) :
```
...$ application install postgresql
```
Ensuite, voici la commande pour lancer PostgreSQL, à faire à chaque séance de TP :
```
...$ application start postgresql
```
Les commandes suivantes ne sont à faire que la première fois pour créer la base de données du TP :
```
...$ createdb -h localhost secondhandcars
...$ curl https://perso.univ-rennes1.fr/pierre.nerzic/BDDA/SecondHandCars.dump | psql -h localhost -d secondhandcars
...$
```
Maintenant, la base `secondhandcars` est prête pour le TP. Voici comment on s’y connecte :
```
...$ psql -h localhost secondhandcars
votrelogin=#
```
Ce prompt est celui du SGBD qui attend des requêtes SQL. Par exemple pour obtenir la liste des tables, tapez ceci. `\l` et `\d` sont des commandes de psql. `\l` affiche la liste des bases de données, `\d` affiche la liste des tables de la base courante.
```
votrelogin=# \l
votrelogin=# \d
votrelogin=# \d secondhandcars
votrelogin=#
```

<div class="alert alert-block alert-danger">
    Gardez bien la fenêtre shell ouverte. Vous <b>devrez arrêter</b> le service PostgreSQL à la fin de <b>chaque séance</b> en faisant ce qui suit, ou en éteignant la machine :
<pre style="padding: 8px;">
votrelogin=# \q
...$ application stop postgresql
</pre>
</div>

### Connexion et requêtes par le cahier Jupyter
Ce qui précède était seulement la mise en place du serveur et des données en shell. Maintenant, c'est ce cahier Jupyter qui va s'y connecter et effectuer des requêtes. On va utiliser une excellente extension appelée __[JupiSQL](https://jupysql.ploomber.io/en/latest/quick-start.html)__.

D'abord, on va vérifier qu'il y a bien l'extension dans votre cahier Jupyter. Exécutez la cellule suivante :

In [ ]:
%load_ext sql
%config SqlMagic.displaycon = False
%config SqlMagic.feedback = 0
%config SqlMagic.displaylimit = 0
%config SqlMagic.named_parameters="enabled"

Il ne doit y avoir aucune erreur, sauf éventuellement un message `The sql extension is already loaded. To reload it, use: %reload_ext sql`. Ne le faites pas. C'est seulement qu'il ne faut évaluer cette cellule qu'une seule fois.

Ensuite, il y a une autre chose à faire une seule fois, c'est de configurer le lien avec la base de données dans la cellule ci-dessous. C'est un widget de connexion. Il va vous dire qu'il enregistre les informations de connexion dans `~/.jupysql/connections.ini`, mais ce fichier n'existe pas au début. Alors faites ceci :

1. cliquez sur `Create new connection`
2. Choisissez `PostgreSQL` au lieu de `DuckDB`
3. Saisissez les infos :
- Connection alias :  `default`
- Username : votre nom de compte
- Password : votre mot de passe
- Host : `localhost`
- Database : `secondhandcars`
- Port : `5432`
4. bouton `Create`


In [ ]:
%sqlcmd connect

Il ne doit pas y avoir d'erreur, seulement un bouton bleu `Connected`. S'il y a seulement  `Connect` alors cliquez dessus. C'est comme ça que ça apparaîtra aux prochaines séances.

La requête suivante doit réussir et afficher 49573.

In [ ]:
%sql SELECT count(*) FROM secondhandcars

Vous voyez qu'il faut seulement faire précéder la requête du mot clé `%sql`. Le `;` final est optionnel.

Si votre requête tient sur plusieurs lignes, alors mettez `%%sql` sur la première ligne. Voici un exemple.

In [ ]:
%%sql
SELECT marque, AVG(prix) AS prix_moyen
FROM secondhandcars
WHERE nb_portes = 4 AND carburant = 'GPL'
GROUP BY marque;

### Requêtes simples
Maintenant à vous. Écrivez les requêtes dans les cellules vides sous les questions ci-dessous.

* Le nombre de tuples dont le prix est inconnu (`NULL`) :

In [ ]:
%sql SELECT 'TODO'

* Le nombre de tuples dont le prix est inférieur à 10 :

In [ ]:
%sql SELECT 'TODO'

* Le nombre de tuples dont le kilométrage (colonne km) est compris entre 10 et 500 (inclus) :

In [ ]:
%sql SELECT 'TODO'

On voit comment les vendeurs cherchent à mettre leur annonce en avant à n'importe quel prix...

On continue avec des requêtes plus difficiles.
* Affichez les valeurs distinctes de l’attribut `annee`, classées dans l'ordre croissant

In [ ]:
%sql SELECT 'TODO'

* Affichez le nombre d'années différentes, c’est à dire le nombre de valeurs de la question précédente (requête imbriquée ou bon emploi des agrégations).

In [ ]:
%sql SELECT 'TODO'

* Affichez un tableau à deux colonnes : les années et le nombre de tuples pour cette année, trié dans l'ordre croissant des années.

In [ ]:
%sql SELECT 'TODO'

### Traitement des résultats par un script Python

Voici comment récupérer un résultat de requête dans une variable. C'est extrêmement simple : une sélection retourne toujours une sorte de liste de tuples Python qu'on peut parcourir par une simple boucle. 

In [ ]:
results = %sql SELECT annee, prix FROM secondhandcars WHERE prix_neuf_moyen > 200000
for result in results:
    print(result)

En fait, le type du résultat n'est pas une liste de tuples Python, mais est de la classe `sql.run.ResultSet`. Ses instances possèdent les propriétés suivantes :

* `results.keys` : retourne les noms des colonnes
* ils implémentent les méthodes des itérateurs, donc on peut parcourir les n-uplets par un `for row in results:`
* `len(results)` retourne le nombre de n-uplets
* `results[i]` : retourne le n-uplet n°i, i commençant à 0
* `results.dicts()` : retourne un itérateur de dictionnaires Python construits sur chaque n-uplet

In [ ]:
results = %sql SELECT annee, marque, prix FROM secondhandcars WHERE prix_neuf_moyen > 200000 ORDER BY prix DESC
print("number of rows =", len(results))
print("keys =", results.keys)
print("second row =", results[1])
print("dicts from results:")
for d in results.dicts():
    print(d)

Et chaque n-uplet obtenu est une sorte d'objet dont les variables membres publiques sont les noms des colonnes. Ainsi, on peut faire :

In [ ]:
print(f"The price of the second most expensive car, a {results[1].marque} of {results[1].annee}, is {results[1].prix}€.")

Voici comment extraire le comptage des n-uplets :

In [ ]:
results = %sql SELECT COUNT(*) FROM secondhandcars WHERE prix_neuf_moyen > 100000
print(f"There are {results[0].count} very expensive cars.")

Lorsque la requête elle-même est une chaîne dans une variable Python, c'est un peu plus bizarre. On ne peut pas faire `%sql my_request`, mais `%sql {{my_request}}`

In [ ]:
my_request = "SELECT COUNT(*) FROM secondhandcars WHERE prix_neuf_moyen > 200000"
%sql {{my_request}}

Et si on a une valeur dans une variable Python, on peut aussi l'insérer dans une requête SQL en l'entourant de `{{var}}`.

In [ ]:
expensive = 150000
%sql SELECT COUNT(*) FROM secondhandcars WHERE prix_neuf_moyen > {{expensive}}

Dans un cahier Jupyter, les variables affectées par une cellule peuvent être utilisées globalement dans la suite. On va avoir besoin d'une variable pour mémoriser le nombre total de n-uplets de la table. Complétez la cellule suivante.

In [ ]:
# query the total number of tuples
results = %sql SELECT COUNT(*) FROM secondhandcars
tot_number_tuples = 1    # TODO
print(f'tot_number_tuples = {tot_number_tuples}')

Pour finir, on peut dessiner un très joli graphique interactif avec Plotly. Voir la **[documentation du Bar Chart](https://plotly.com/python/bar-charts/)**.

In [ ]:
results = %sql SELECT annee, COUNT(*) FROM secondhandcars GROUP BY annee ORDER BY annee
import plotly.express as px
px.bar(results, x="annee", y="count")

***

## Partie 1 : Estimation de cardinalités à l’aide des métadonnées

Au cours de cette première partie du TP vous allez effectuer quelques expérimentations sur le planificateur et l’optimiseur de requêtes de PostgreSQL.

### Utilisation ou non des index sur les données

Dans la table SecondHandCars l’attribut prix est associé à une structure d’indexation permettant au moteur d’exécution de PostgreSQL d’optimiser des sélections sur cet attribut. Les valeurs des autres attributs ne sont pas indexées.

Voici la requête SQL qui permet de lister les index existants sur les colonnes d'une table. Cette requête utilise une *métatable* appelée `pg_indexes`. Une métatable est une table qui décrit d'autres tables ou les colonnes d'une autre table. Ses colonnes, `indexname`, `indexdef` décrivent les index existants, le nom et la requête qui a servi à le créer.

In [ ]:
%sql SELECT indexname, indexdef FROM pg_indexes WHERE tablename = 'secondhandcars'

L’instruction `EXPLAIN requête` affiche le plan d’exécution d’une requête, c’est à dire la stratégie suivie par le SGBD pour évaluer la requête. On peut ajouter le mot clé `ANALYZE` après `EXPLAIN` pour obtenir des estimations sur le temps de calcul, c’est à dire : `EXPLAIN ANALYZE requête`

Par exemple :

In [ ]:
%sql EXPLAIN SELECT * FROM secondhandcars WHERE puissance_ch < 200

In [ ]:
%sql EXPLAIN ANALYZE SELECT * FROM secondhandcars WHERE puissance_ch < 200

<div class="alert alert-block alert-warning">
    Attention, les requêtes à expliquer ne sont pas celles de comptage, mais celles qui retournent des n-uplets. C'est à dire <samp>EXPLAIN SELECT * FROM</samp> et non pas <samp>EXPLAIN SELECT COUNT(*) FROM</samp>
</div>

D’autre part, cela n’est intéressant que s’il y a un index sur les colonnes concernées par la clause where. On ne va pas toucher à la colonne `puissance_ch`, mais `prix_neuf_moyen`. D'abord, on supprime tout index existant (au cas où).

In [ ]:
%sql DROP INDEX IF EXISTS idx_prix_neuf_moyen

In [ ]:
%sql EXPLAIN SELECT * FROM secondhandcars WHERE prix_neuf_moyen < 5000

Notez bien `Seq Scan on secondhandcars`

In [ ]:
%sql CREATE INDEX idx_prix_neuf_moyen ON secondhandcars(prix_neuf_moyen)

In [ ]:
%sql EXPLAIN SELECT * FROM secondhandcars WHERE prix_neuf_moyen < 5000

Cette fois, c'est `Bitmap Heap Scan on secondhandcars`.

Sans rentrer dans tous les détails techniques, vous allez observer deux stratégies d’exécution.
* « Seq Scan », c’est à dire un parcours exhaustif des n-uplets pas efficace et dont il n'y a rien à dire.
* « Bitmap Heap Scan » qui est un parcours à deux niveaux beaucoup plus rapide.

La stratégie Bitmap Scan est sur 4 lignes à lire de bas en haut. Ça commence d’abord 3e ligne par un « Bitmap Index Scan » qui consiste en un parcours des « pages » contenant les n-uplets susceptibles d’être sélectionnés par la condition « Index Cond » 4e ligne.

C’est à dire que les n-uplets sont groupés dans le stockage interne (disque dur) pour former des pages. Une page fait 8 Ko, `SELECT current_setting('block_size');` voir ci-dessous. Une page contient donc un certain nombre de n-uplets. Certaines pages contiennent des n-uplets utiles, d’autres aucun. L’index contient un « bitmap » qui indique lesquelles sont pertinentes. C’est comme un tableau de booléens, un par valeur remarquable présente dans l’index, qui indiquent dans quelles pages on trouve cette valeur. Par exemple qu’on trouve des annonces pour des voitures dont le prix_neuf_moyen convient dans telles et telles pages sur le disque. Vous comprenez que ce mécanisme occupe de la place mais il accélère considérablement les recherches quand on peut l'utiliser.

In [ ]:
%sql SELECT current_setting('block_size') AS block_size

Donc il y a d’abord cette sélection des pages contenant les données qu'on cherche, puis en remontant, il y a un « Recheck Cond » 2e ligne pour vérifier la condition individuellement sur les n-uplets des pages choisies.

Vous trouverez tout le détail des explications dans __[la documentation de référence sur les plans d'exécution](https://www.postgresql.org/docs/current/using-explain.html)__. Et __[cette page](https://www.cybertec-postgresql.com/en/postgresql-indexing-index-scan-vs-bitmap-scan-vs-sequential-scan-basics/)__ résume le tout avec des schémas.

La bascule entre les deux stratégies, « Seq Scan » ou « Bitmap Scan » dépend du nombre attendu de n-uplets et leur répartition dans les pages. Il vaut mieux faire un parcours exhaustif si on prévoit que beaucoup de n-uplets vont satisfaire la condition where, et utiliser le bitmap s’il y en a peu, de préférence répartis sur peu de pages différentes. Mais évidemment, il faut qu'il y ait un bitmap pour les valeurs recherchées. Les critères complets sont dans __[la documentation de référence, statistiques utilisées](https://www.postgresql.org/docs/current/planner-stats.html)__.

On va étudier l'emploi ou non des index pour accélérer les requêtes. C'est selon les perspectives d'avoir un gain de vitesse, et donc c'est en estimant la proportion des données sélectionnées. On veut essayer de savoir si le SGBD se base sur le nombre relatif de n-uplets.

On va dérouler l'algorithme suivant sur plusieurs requêtes et voir ce qu'il est est

1. On demande le nombre total de n-uplets dans la table
2. On exécute la requête et on compte le nombre de n-uplets qu'elle retourne
3. On rapporte ce nombre au nombre total de n-uplets dans la table : on obtient un réel entre 0 et 1 qu'on appelle *cardinalité relative*.
4. On demande quelle est la stratégie pour sélectionner les n-uplets : Seq Scan ou Bitmap Heap Scan

À priori, ça devrait être le Bitmap Heap Scan quand la cardinalité relative est faible.

Complétez la fonction suivante qui déroule l'algorithme.

In [ ]:
def PrintKindOfScan(query):
    "displays the relative cardinality and the first line of the execution plan of the query"
    # 1. total number of tuples in the table
    global tot_number_tuples
    # print the query
    print(query)
    # 2. get the tuples selected by the request
    results = %sql {{query}}
    # 3. compute the relative cardinality
    rel_card = 0    # TODO
    print(f"  relative cardinality is {rel_card:.3f}")
    # 4. analyze the request and get the strategy
    analysis = %sql EXPLAIN {{query}}
    print(f"  {analysis[0][0]}")

On applique cette fonction à plusieurs requêtes.

In [ ]:
PrintKindOfScan("SELECT * FROM secondhandcars WHERE prix BETWEEN 3000 AND 7500")
PrintKindOfScan("SELECT * FROM secondhandcars WHERE prix BETWEEN 3500 AND 12000")
PrintKindOfScan("SELECT * FROM secondhandcars WHERE prix < 17500")
PrintKindOfScan("SELECT * FROM secondhandcars WHERE prix > 9000")
PrintKindOfScan("SELECT * FROM secondhandcars WHERE prix > 250000")

Il semble qu'on puisse en déduire que le SGBD utilise le Bitmap Scan lorsque la cardinalité relative est inférieure à 0,5. Mais la question est alors : comment le SGBD peut-il calculer la cardinalité relative alors que la requête n'est pas encore exécutée ? Il faut impérativement estimer cette cardinalité à partir de la condition de sélection.

### Histogramme de la distribution des données

La réponse, c'est que le SGBD maintient des statistiques sur la distribution des données, dans une métatable. C'est par exemple l'histogramme des valeurs de l'attribut, comme le suivant qui montre la distribution des prix.

In [ ]:
results = %sql SELECT prix FROM secondhandcars WHERE prix < 100000
import plotly.express as px
px.histogram(results, x="prix", nbins=80)

Avec cet histogramme, on peut estimer la cardinalité d'une condition comme prix < 3500. Il suffit de cumuler les barres entre 0 et 3500.

Alors PostgreSQL utilise effectivement un histogramme, mais il n'a pas cette apparence. Le précédent est qualifié d'*equiwidth*, car les barres ont toutes la même largeur, et leur hauteur représente le nombre de données dans l'intervalle. Il existe aussi des histogrammes *equidepth* dont le principe est que toutes les barres représentent la même quantité de données, et donc les barres sont plus ou moins larges.

Voici comment extraire cet histogramme de la métatable. C'est un peu compliqué, parce que la colonne `histogram_bounds` de la table `pg_stats` est un tableau -- c'est possible avec PostgreSQL. Pour obtenir ce tableau sous la forme de valeurs séparées, on utilise la fonction `unnest` __[documentée ici](https://www.postgresql.org/docs/current/functions-array.html#ARRAY-FUNCTIONS-TABLE)__ ; et il faut indiquer en détail quel est le type des valeurs recherchées, des `int` qui sont écrits dans un texte, voir __[cette explication](https://stackoverflow.com/a/70782751)__.<a id='mycell'></a>

In [ ]:
%sql SELECT unnest(histogram_bounds::text::int[]) AS bounds FROM pg_stats WHERE tablename='secondhandcars' AND attname='prix' LIMIT 10

NB: la requête précédente extrait seulement les 10 premières bornes, c'est à dire les 9 premiers intervalles. Le script suivant dessine les 15 premiers intervalles. 

In [ ]:
# histogram extraction of the first 15 intervals (16 bounds)
query = """SELECT unnest(histogram_bounds::text::int[]) AS bounds
        FROM pg_stats WHERE tablename='secondhandcars' AND attname='prix'
        LIMIT 16"""
bounds = %sql {{query}}

# convert successive bounds to interval list
histogram_bars = []
b1 = None
for b2 in bounds:
    if b1 is not None:
        histogram_bars.append({'from': b1.bounds, 'to': b2.bounds, 'height': 1, 'text': f']{b1.bounds}, { b2.bounds}]'})
    b1 = b2

# convert to Pandas DataFrame to be displayed with Plotly
import pandas
df = pandas.DataFrame(histogram_bars)

# draw a Bar Chart
import plotly.graph_objects as go
figure = go.Figure()
figure.add_trace(
    go.Bar(
        x=((df["from"]+df["to"])/2).to_list(),
        y=df["height"],
        width=(df["to"]-df["from"]).to_list(),
        text=df["text"],
    )
)

Dans le graphique précédent, chaque barre représente approximativement la même quantité de données. Il faut bien comprendre que ce ne sont que des estimations collectées très rapidement, donc imprécises. D'autre part, les bornes peuvent changer d'une séance à l'autre. C'est la requête SQL `ANALYZE;` qui relance le recueil des métadonnées.

Exécutez la cellule suivante, puis ré-exécutez les cellules à partir de la [[35]](#mycell). Il est possible que vous observiez des changements (ou pas). C'est pourquoi dans la suite, vos résultats seront un peu différents de ceux des voisins.

In [ ]:
%sql ANALYZE;

Remarquez que cette commande est très rapide. Elle utilise la manière dont les données sont rangées en mémoire sans les parcourir une à une. C'est pour cela qu'elle ne recueille que des estimations.

### Vérification de la qualité de l'histogramme equidepth

Par curiosité, on va regarder ce qu'il en est de la cardinalité exacte de quelques unes de ces barres. On reprend la variable `histogram_bars`. C'est un tableau de bornes `from`, `to`. On va demander le nombre de n-uplets situés dans ces bornes. Cependant, on va considérer que `from` est exclu car il ne faut pas que les mêmes n-uplets soient comptés dans deux barres, lorsque leur prix est à la frontière.

In [ ]:
# sum of counts
total_count = 0
# loop on bars
for bar in histogram_bars:
    # query the actual cardinality of this bar
    results = %sql # TODO query the number of cars that have their prix inside bar, limits are bar["from"] and bar["to"]
    bar_count = 0  # TODO get the number of cars in results
    # accumulate bar_count in total_count
    # TODO update total_count
    # display the results
    print(f'{bar["text"]:15}: {bar_count} tuples')
# average count
print(f'average count per interval = {total_count / len(histogram_bars):.3f}')

On voit une liste d'intervalles. Ce sont les bornes de l'histogramme. On voit aussi le véritable nombre de tuples qu'il y a dans chaque intervalle. Les résultats semblent extrêmement bizarres, très variables, loin de la définition d'un histogramme *equidepth*, même en considérant que ce ne sont que des estimations. Normalement, on devrait avoir à peu près le même nombre de tuples par intervalle, car les bornes sont ajustées pour cela, au contraire d'un histogramme *equiwidth* dont on force les bornes à des intervalles réguliers et où le nombre de n-uplets varie beaucoup.

Alors déjà, il est possible que les données soient très mal réparties et qu'il soit impossible de faire un tel histogramme quand il y a de très nombreuses valeurs identiques impossibles à placer dans des intervalles distincts. Ça pourrait expliquer les inégalités, car les vendeurs de voitures ont tendance à arrondir le prix.

Ceci étant, même si l'histogramme est très approximatif, il permet quand même d'estimer des cardinalités. En effet, s'il y a 100 intervalles, (100+1 bornes) dans cet histogramme (le programme précédent n'en montre que 15. Les presque 50000 n-uplets de la table sont distribués sur ces 100 intervalles, soient presque 500 par intervalle. C'est à peu près la moyenne qu'on observe. Il semble que les bornes soient seulement un peu mal placées.

### Valeurs absentes (null)

Mais il semble qu'il manque quelque chose. La moyenne du nombre de n-uplets par intervalle est un peu faible, environ 465 au lieu de 495. Au niveau de l'ensemble des données, ça représente seulement 465*100 n-uplets au lieu de 49573. On va voir pourquoi dans tout ce qui suit.

D'abord, il y a des valeurs `null` dans la colonne prix. Ces valeurs sont évidemment absentes de l'histogramme, ce qui pourrait expliquer la moyenne plus basse. Ecrivez la requête qui compte les valeurs nulles dans la colonne prix.

In [ ]:
actual_null_count = 0  # TODO SQL query to get the number of cars that have null prix 
print(f'actual_null_count = {actual_null_count}')

Le nombre est assez petit, donc il manque encore autre chose pour expliquer la mauvaise disposition apparente des bornes de l'histogramme. On va le voir dans la prochaine section.

Parmi les métadonnées de PostgreSQL, il y a aussi une estimation du nombre de valeurs nulles pour chaque colonne. Voici la requête pour le connaître.

In [ ]:
results = %sql SELECT null_frac FROM pg_stats WHERE tablename='secondhandcars' AND attname='prix'
est_null_card = results[0].null_frac
est_null_count = round(est_null_card * tot_number_tuples)
print(f'est_null_count = {est_null_count}, error = {100 * abs(est_null_count - actual_null_count) / actual_null_count:.2f}%')

`est_null_card` est la cardinalité relative estimée des valeurs nulles. On voit que la cardinalité absolue estimée, `est_null_count` est proche de la véritable cardinalité, mais elle ne suffit pas à expliquer l'écart entre la cardinalité réelle des bornes et la répartition irrégulière des bornes de l'histogramme, car il manque environ 3000 n-uplets (46500 au lieu de 49573).

### Valeurs fréquentes

PostgreSQL mémorise aussi une liste des valeurs les plus fréquentes rencontrées parmi les données. Par défaut, ce sont les 100 valeurs les plus fréquentes du prix (parce qu'il y a un index sur la colonne prix). Voici comment l'obtenir. C'est une requête bien plus complexe car les valeurs fréquentes et leur cardinalités sont dans deux colonnes différentes de la table `pg_stats`.

In [ ]:
%%sql
SELECT * FROM (
  SELECT unnest(most_common_vals::text::int[]) AS val,
         unnest(most_common_freqs) AS freq,
         round(unnest(most_common_freqs) * 49573) AS card    --- À ENLEVER
  FROM pg_stats WHERE tablename = 'secondhandcars' AND attname = 'prix'
) AS val_freq_table
ORDER BY val

La colonne `val` contient des valeurs qui ont été souvent rencontrées dans les données. Par exemple, un prix de 9990€ semble très fréquent, 560 fois, et 10500€ est rencontré pour 496 voitures -- Attention, vos valeurs sont probablement légèrement différentes.

Dans la cellule suivante, mettez le prix le plus fréquent et sa cardinalité absolue estimée selon les métadonnées de votre base. C'est nettement plus facile en modifiant la requête précédente pour trier les fréquences dans l'ordre décroissant et en affichant aussi la cardinalité absolue.

<div class="alert alert-block alert-success"><span style='font-size:24px;'>&#9997;&nbsp;</span>
prix: ..., cardinalité absolue estimée ...
</div>

Comme pour la cardinalité des valeurs nulles, vérifions rapidement quelques valeurs fréquentes avec le script suivant, à compléter.

In [ ]:
# put most common values and their frequencies into an array
query = """
SELECT * FROM (
  SELECT unnest(most_common_vals::text::int[]) AS val,
         unnest(most_common_freqs) AS freq
  FROM pg_stats WHERE tablename = 'secondhandcars' AND attname = 'prix'
) AS val_freq_table
ORDER BY val
"""
most_common_vals_freqs = %sql {{query}}

# query the actual cardinality of some of these values
import random
for _ in range(8):
    # pick a random pair of a value and its estimated relative cardinality
    value, est_rel_card = random.choice(most_common_vals_freqs)
    est_abs_card = round(est_rel_card * tot_number_tuples)
    # TODO query its actual absolute cardinality (number of cars that have prix = value)
    act_abs_card = 0  # TODO
    # % of relative error
    rel_error = abs(est_abs_card - act_abs_card) / act_abs_card * 100
    # display results
    print(f'{value:8}: estimated={est_abs_card}, actual={act_abs_card}, error={rel_error:5.2f}%')

On constate quelques écarts, mais globalement, c'est assez fiable. Une erreur de 10% conduirait le SGBD à choisir la mauvaise stratégie pour évaluer la requête, mais sans causer un lourd fardeau de calcul, car l'autre stratégie n'aurait pas été beaucoup plus rapide.

Voici le calcul précédent mis dans une fonction plus générale qui servira plus loin.

In [ ]:
def getMostCommonValsFreqs(tablename, attribute):
    "returns the most common values and their frequencies as a table"
    query = f"""SELECT
            unnest(most_common_vals::text::int[]) AS val,
            unnest(most_common_freqs) AS freq
        FROM pg_stats WHERE tablename='{tablename}' AND attname='{attribute}'"""
    result = %sql {{query}}
    return result

print(getMostCommonValsFreqs('secondhandcars', 'prix'))

Ces valeurs fréquentes sont comme retirées des données avant de construire l'histogramme. C'est à dire qu'en rajoutant ces valeurs à l'histogramme, les cardinalités des barres redeviendraient plus régulières. Mais on va clarifier et vérifier tout cela. Nous allons vérifier ces informations et mieux comprendre comment PostgreSQL parvient à décider très rapidement s'il est préférable de faire un parcours complet ou d'utiliser les bitmaps de l'index.

### Estimation des cardinalités

Ainsi lorsqu'il y a un index sur une colonne, le SGBD mémorise trois types d'informations complémentaires (métadonnées) :
- la cardinalité relative estimée des valeurs null,
- les 100 valeurs les plus fréquentes et leur cardinalité relative approximative,
- 100 intervalles, chacun approximativement de même cardinalité relative, $\text{bar\_rel\_card}$ qui exclut les valeurs fréquentes.

On a donc avoir l'équation suivante entre toutes ces estimations :

(1)&emsp; $\normalsize\text{est\_null\_card} + \sum_{\text{most\_common\_vals}}\text{most\_common\_freqs} + 100 * \text{bar\_rel\_card} = 1$

C'est à dire que les cardinalités relatives estimées de toutes ces catégories représentent la totalité des données.

On peut donc obtenir $\text{bar\_rel\_card}$ simplement par :

$\text{bar\_rel\_card} = \Large\frac{1 - \text{est\_null\_card} + \sum_{\text{most\_common\_vals}}\text{most\_common\_freqs}}{100}$

NB: le dénominateur, 100 est le nombre de barres par défaut dans PostgreSQL. Il peut être modifié par l'utilisateur, voir __[default_statistics_target](https://www.postgresql.org/docs/current/runtime-config-query.html#GUC-DEFAULT-STATISTICS-TARGET)__.

Compléter le programme suivant qui calcule $\text{bar\_rel\_card}$. Notez qu'on le rend polyvalent avec des paramètres. On a placé le calcul des valeurs fréquentes dans une fonction.

In [ ]:
def getBarRelCardinality(tablename, attribute):
    "returns the estimated cardinality of each bar in the equidepth histogram of attribute in tablename"
    # get the null cardinality estimation from the metadata
    est_null_card = 0  # TODO
    # get only the most common values frequencies
    results = %sql SELECT unnest(most_common_freqs) AS freq FROM pg_stats WHERE tablename='{{tablename}}' AND attname='{{attribute}}'
    # compute 1 - null cardinality - sum(all frequencies)
    est_card_sum = 1.0  # TODO
    # get the number of bars in the histogram = 1 - number of bounds
    query = f"""SELECT (SELECT COUNT(*)
            FROM unnest(histogram_bounds::text::int[])) AS count
            FROM pg_stats WHERE tablename='{tablename}' AND attname='{attribute}'"""
    bar_count = 1  # TODO number of bars obtained from the query, but beware, query returns the number of bounds
    # divide by the number of bars
    # TODO
    return est_card_sum

bar_rel_card = getBarRelCardinality('secondhandcars', 'prix')
print(f'relative cardinality of each bar in the histogram = {bar_rel_card:.6f}')

Voila la cardinalité relative estimée de chaque barre dans l'histogramme equidepth géré par PostgreSQL.

On va maintenant vérifier la précision des estimations sur des plages de données, pour des conditions de filtrage comme `WHERE prix BETWEEN b1 AND b2`. Pour cela, il faut appliquer l'équation (1). Donc additionner toutes les cardinalités relatives des valeurs fréquentes qui font partie de l'intervalle, et y ajouter le nombre de barres qui sont dans l'intervalle.

Voici un schéma de la situation. L'histogramme contient un certain nombre de barres pas toutes dessinées, et les bornes b1 et b2 sont quelque part dans ces barres. La barre du début d'intervalle, en rose est coupée, comme la barre de fin en orange. Les barres en vert sont entièrement incluses dans l'intervalle.

<img style="margin: auto;" src='data:image/svg+xml;utf8,<svg xmlns="http://www.w3.org/2000/svg" width="400" viewBox="-2 -1 60 14.2"><g transform="translate(-4,-2.4)" style="fill-opacity:1;stroke:black;stroke-width:0.25;stroke-linecap:round;font-size:3px;"><rect style="fill:lightgray;" width="11.2" height="7.9" x="0.8" y="2.6"/><rect style="fill:lightpink;" width="6.6" height="7.9" x="12" y="2.6"/><rect style="fill:lightgreen;" width="9" height="7.9" x="18.5" y="2.6"/><rect style="fill:lightgreen;" width="10" height="7.9" x="27.5" y="2.6"/><rect style="fill:lightgreen;" width="7" height="7.9" x="37.5" y="2.6"/><rect style="fill:gold;" width="12" height="7.9" x="44" y="2.6"/><rect style="fill:lightgray;" width="8" height="7.9" x="56" y="2.6"/><rect style="fill:chartreuse;fill-opacity:0.4;" width="32" height="10" x="15" y="1.6"/><text x="13" y="15.3">b1</text><text x="45" y="15.3">b2</text></g></svg>'>

Chaque barre représente la cardinalité relative obtenue plus haut, cellule #75. Il faut donc comptabiliser une partie de la barre rose, toutes les barres vertes et une partie de la barre orange. Pour ces deux barres extrêmes, on considère que les données sont réparties uniformément, et donc c'est en proportion de la couverture de la barre par l'intervalle. Il faut également ajouter les cardinalités relatives des valeurs fréquentes qui sont comprises entre b1 et b2.

Voici un programme à compléter. Il doit retourner la cardinalité relative de la condition `WHERE attribute BETWEEN b1 AND b2`.

In [ ]:
def getHistogramBounds(tablename, attribute):
    "returns the bounds of the equidepth histogram of attribute in tablename"
    # query histogram_bounds from database
    query = f"""SELECT unnest(histogram_bounds::text::int[]) AS bounds
            FROM pg_stats WHERE tablename='{tablename}' AND attname='{attribute}'"""
    bounds = %sql {{query}}
    # build histogram_bars = list of dict{from, to, height, text}
    histogram_bars = []
    b1 = None
    for b2 in bounds:
        if b1 is not None:
            histogram_bars.append({'from': b1.bounds, 'to': b2.bounds, 'height': 1, 'text': f']{b1.bounds}, { b2.bounds}]'})
        b1 = b2
    return histogram_bars

def getIntervalRelativeCardinalityV1(tablename, attribute, b1, b2):
    "computes the estimation of the relative cardinality of attribute between b1 and b2" 
    # parameters errors check
    if b1 > b2: return 0.0
    # future result
    cardinality = 0.0
    # histogram bars and cardinality
    histogram_bars = getHistogramBounds(tablename, attribute)
    bar_rel_card = getBarRelCardinality(tablename, attribute)
    # count histogram bars that cover interval [b1, b2]
    for bar in histogram_bars:
        # TODO cardinality += intersection of [b1, b2] and bar * bar_rel_card
    # add cardinality of common values that are between b1 and b2
    most_common_vals_freqs = getMostCommonValsFreqs(tablename, attribute)
    # TODO loop on pairs (val,freq) in most_common_vals_freqs
    # result
    return cardinality


# apply this on some examples
for b1,b2 in [(0, 1000), (1000, 2000), (2000, 3000), (500, 5000), (1200, 4500), (5000, 12000), (8000, 20000)]:
    # estimated cardinality, relative and absolute
    est_rel_card = getIntervalRelativeCardinalityV1('secondhandcars', 'prix', b1, b2)
    est_abs_card = round(est_rel_card * tot_number_tuples)
    # actual cardinality
    act_abs_card = 1  # TODO count cars whose prix is in [b1, b2]
    # % of relative error
    rel_error = abs(est_abs_card - act_abs_card) / act_abs_card * 100
    # display results
    print(f'prix between {b1} and {b2}:\t{est_rel_card:.3} = {est_abs_card} tuples, actual = {act_abs_card} tuples, error={rel_error:5.2f}%')

Normalement, vos taux d'erreur doivent être assez petits, moins de 5%. Si vous avez de plus grandes erreurs, il y a des chances que ça soit votre programme qui calcule mal. Avez-vous bien compté les barres, et celles qui sont partiellement couvertes ? Ajoutez des affichages pour la mise au point.

C'est de cette manière que PostgreSQL évalue la *sélectivité* des conditions de filtrage. Il décide si un parcours complet est préfèrable ou l'utilisation de l'index. L'algorithme est très rapide, même s'il y a 100 valeurs fréquentes et 100 barres d'histogramme.

L'algorithme de `getIntervalRelativeCardinalityV1` fonctionne bien, mais dans certains cas de distributions très particulières des données, les bornes de l'histogramme sont confondues, comme empilées au même endroit pour représenter des densités exceptionnelles. Dans ces cas, l'algorithme ne va pas car il s'arrête au premier intervalle contenant b2, alors qu'il peut y en avoir plusieurs à la suite.

Voici une autre idée, pour une version de la fonction. Elle consiste à écrire que la cardinalité de [b1, b2], $card(\,[b1, b2]\,) = card(\,]{-\infty}, b2]\,) - card(\,]{-\infty}, b1[\,)$. C'est à dire qu'on va calculer la cardinalité relative en dessous d'une borne, ou jusqu'à une borne, faire ça pour b1 et b2 et soustraire les deux cardinalités.

On commence par la fonction qui calcule la cardinalité en dessous de (strict=True) ou jusqu'à (strict=False) une borne b.

In [ ]:
def getEstimatedCardinalityLessThan(tablename, attribute, b, strict):
    "retourne la cardinalité estimée de ]-∞, b[ si strict=True, sinon ]-∞, b]"
    # histogram bars and cardinality
    histogram_bars = getHistogramBounds(tablename, attribute)
    bar_rel_card = getBarRelCardinality(tablename, attribute)
    # count full and partial bars ]b1, b2] so that b2 <= b
    bar_nb = 0  # TODO loop on histogram_bars
    # relative cardinality of all bars before b, and including b if strict is False
    cardinality = bar_nb * bar_rel_card
    # common values less than (or equal to if strict is False) v
    most_common_vals_freqs = getMostCommonValsFreqs(tablename, attribute)
    # TODO loop on pairs (val,freq) in most_common_vals_freqs
    # final result
    return cardinality

# test this on some examples
import random
for b in sorted([int(random.weibullvariate(10000, 1)) for _ in range(6)]):
    # estimated cardinality, relative and absolute
    est_rel_card = getEstimatedCardinalityLessThan('secondhandcars', 'prix', b, False)  # try with strict=True
    est_abs_card = round(est_rel_card * tot_number_tuples)
    # actual cardinality, put < when strict is True
    act_abs_card = 1  # TODO count cars whose prix is less or equal to b # or less than if strict is True
    # % of relative error
    rel_error = abs(est_abs_card - act_abs_card) / act_abs_card * 100
    # display results
    print(f'prix < {b}:\t{est_rel_card:.3} = {est_abs_card} tuples, actual = {act_abs_card} tuples, error={rel_error:5.2f}%')

Noter que l'erreur peut être très grande lorsque la borne est basse (<100), car il n'y a qu'une seule barre dans l'histogramme pour représenter un grand nombre de voitures. Mais ce n'est pas très grave pour la suite. D'abord, il y a peu de n-uplets dans cette zone et d'autre part, si on cherche sur un intervalle [b1, b2], cette erreur sur l'une des bornes s'annulera avec celle de l'autre.

Il reste à calculer la cardinalité d'un intervalle [b1, b2] en soustrayant la cardinalité jusqu'à b2 inclus et celle inférieure à b1.

In [ ]:
def getIntervalRelativeCardinalityV2(tablename, attribute, b1, b2):
    "retourne la cardinalité estimée de [b1, b2]"
    cardb1 = 0  # TODO call getEstimatedCardinalityLessThan on b1
    cardb2 = 0  # TODO call getEstimatedCardinalityLessThan on b2
    return cardb2 - cardb1


# apply this on some examples
for b1,b2 in [(0, 1000), (1000, 2000), (2000, 3000), (500, 5000), (1200, 4500), (5000, 12000), (8000, 20000)]:
    # estimated cardinality, relative and absolute
    est_rel_card = getIntervalRelativeCardinalityV2('secondhandcars', 'prix', b1, b2)
    est_abs_card = round(est_rel_card * tot_number_tuples)
    # actual cardinality
    act_abs_card = 1  # TODO
    # % of relative error
    rel_error = abs(est_abs_card - act_abs_card) / act_abs_card * 100
    # display results
    print(f'prix between {b1} and {b2}:\t{est_rel_card:.3} = {est_abs_card} tuples, actual = {act_abs_card} tuples, error={rel_error:5.2f}%')

Les résultats doivent être très proches de ceux obtenus par la méthode V1. Les données de cette base ne permettent pas de justifier le bien-fondé de la seconde méthode, mais ils apparaîssent très nettement avec des distributions très inégales.

## Partie 2 : Requêtes flexibles

Vous allez maintenant écrire vos premières requêtes flexibles. Vous allez considérer que vous cherchez la voiture la moins chère possible, ayant le moins de kilomètres possible et la plus récente possible. Vous allez définir les fonctions caractéristiques des ensembles flous correspondant à ces trois notions en utilisant des fonctions écrites en pl/pgsql.

Nous allons utiliser les index, afin d'optimiser le temps de calcul des requêtes. Dans la cellule suivante, faites créer deux index, l'un sur le kilométrage (colonne `km`), l'autre sur l'année (colonne `annee`). Pensez aux options qui permettent d'éviter les erreurs si ces index existent déjà.

In [ ]:
# TODO (re)create index idx_km on km
# TODO (re)create index idx_annee on annee

### Exemple : Faible kilométrage

Voici l'exemple d'une fonction enregistrée dans le SGBD. 

In [ ]:
%%sql
CREATE OR REPLACE FUNCTION low_mileage(km integer) RETURNS float AS
$$
BEGIN
    IF (km IS NULL) THEN 
        RETURN 0.0;
    END IF;
    IF (km >= 15000) THEN 
        RETURN 0.0;
    END IF;
    RETURN (15000 - CAST(km AS FLOAT))/15000;
END;
$$ 
LANGUAGE plpgsql

Voici l'application de cette fonction à plusieurs kilométrages.

In [ ]:
for km in [500, 2000, 3000, 8000, 20000]:
    result = %sql SELECT low_mileage({{km}}) AS mu
    print(f"µlow_mileage({km} km) = {result[0].mu:.3f}")

C'est à dire qu'un kilométrage de 8000 km n'est pas pleinement « faible », il l'est seulement « moyennement ». La fonction $\mu_{\text{low mileage}}(km)$ est linéaire par morceaux, valant 1 pour 0 km et valant 0 pour 15000 km et au delà.



Voici un exemple d'utilisation de cette fonction dans une requête plus complète.

In [ ]:
%%sql
SELECT COUNT(*), km, round(low_mileage(km)::numeric, 3) AS mu
FROM secondhandcars
WHERE low_mileage(km) > 0.9
GROUP BY km
ORDER BY mu DESC

Notez qu'un paramètre `null` retourne 0.

Une remarque qu'on peut se faire est que les fonctions d'appartenance ne vérifient pas la colonne qu'on leur soumet ; c'est une source d'erreurs.

### Fonctions d'appartenance floue

Définissez maintenant, dans les cellules suivantes les fonctions demandées. Vous avez toute liberté pour définir les bornes floues : supports et noyaux.
    
#### Voitures pas chères

Il faudrait définir une fonction qui se comporte ainsi, mais à vous de choisir la borne.
    


In [ ]:
%%sql
CREATE OR REPLACE FUNCTION cheap_price(prix integer) RETURNS float AS
$$
BEGIN
    RETURN CASE
        WHEN prix IS NULL THEN 0.0
        WHEN prix < 3 THEN 1.0
        ELSE 0.5
    END;
END;
$$ 
LANGUAGE plpgsql

Vous avez remarqué la forme plus compacte pour une conditionnelle multiple.

Dans la cellule suivante, écrivez une requête SQL recherchant les voitures de la marque Saab et ayant un degré $\mu_{\text{cheap\_price}}>0.8$.

In [ ]:
%sql SELECT 'TODO'

#### Voitures ayant un kilométrage modéré

On voudrait une fonction d'appartenance floue ressemblant à ce trapèze, à vous de choisir toutes les bornes.



In [ ]:
%%sql
CREATE OR REPLACE FUNCTION moderate_mileage(km integer) RETURNS float AS
$$
BEGIN
    RETURN CASE
        WHEN km IS NULL THEN 0.0
        ELSE 0.0
    END;
END;
$$
LANGUAGE plpgsql

Dans la cellule suivante, écrivez une requête SQL recherchant les voitures de 2008, roulant au GPL (colonne `carburant`) et ayant un kilométrage modérée à plus de $0.8$.

In [ ]:
%sql SELECT 'TODO'

#### Voitures récentes

On voudrait une fonction d'appartenance floue basée sur l'année qui qualifie les voitures récentes. Cependant l'année, dans cette table, n'est pas un entier mais une chaîne de caractère, un `varchar`. Donc on ne peut pas utiliser de fonction mathématique linéaire, sauf en analysant la chaîne pour la convertir en entier ce qui ne serait pas très rapide sur une grande base de données. Il est préférable de faire des catégories.

D'autre part, la dernière année dans la table est 2011, donc une voiture considérée comme « récente » dans ce TP, est relative à cette date.

In [ ]:
%%sql
CREATE OR REPLACE FUNCTION recent_car(annee varchar) RETURNS float AS
$$
BEGIN
    RETURN CASE
        WHEN annee IS NULL THEN 0.0
        WHEN annee='2011' THEN 1.0
        ELSE 0.0
    END;
END;
$$ 
LANGUAGE plpgsql

Dans la cellule suivante, écrivez une requête SQL recherchant les voitures récentes (µ>0.8), de moins de 90 ch et ayant 2 portes.

In [ ]:
%sql SELECT 'TODO'

### Conditions de sélection floues multiples

Dans les questions précédentes, il n'y avait qu'un seul critère d'appartenance flou recherché avec des critères non-flous. Voyons comment écrire des requêtes conjonctives floues. Si on a 3 fonctions floues, $ft1$, $ft2$ et $ft3$ sur trois attributs $a1$, $a2$ et $a3$, on peut programmer ceci pour obtenir les n-uplets qui satisfont la conjonction des trois fonctions à un degré > 0.8 :
```
SELECT * FROM secondhandcars WHERE ft1(a1) > 0.8 AND ft2(a2) > 0.8 AND ft3(a3) > 0.8
```
C'est une écriture « expansée » pour la T-norme $\min$. En SQL, SQL, le minimum de plusieurs attributs d’un même n-uplet est obtenu par LEAST et non pas MIN qui cherche la plus petite valeur parmi des n-uplets différents. Donc voici comment écrire la requête floue avec la T-norme.
```
SELECT * FROM secondhandcars WHERE LEAST(ft1(a1), ft2(a2), ft3(a3)) > 0.8
```

Écrivez dans la cellule suivante la requête qui affiche les voitures ayant à la fois un faible kimométrage, un prix faible et une année récente, à µ > 0.2. Il est possible qu'il n'y ait aucun résultat si vos bornes des supports et noyaux de vos fonctions d'appartenance sont trop strictes. Modifiez alors leurs définitions pour arriver à un résultat non vide. 

In [ ]:
%sql SELECT 'TODO'

### Analyse des plans d'exécution

Écrivez dans la cellule suivante la requête qui affiche le plan d’exécution d’une requête retournant les voitures de faible kilométrage pour µ > 0.8 :

In [ ]:
%sql EXPLAIN SELECT 'TODO'

Quelle serait la stratégie pour la requête non floue qui demanderait par exemple les voitures dont le kilométrage est inférieur à 12000 km ?

In [ ]:
%sql EXPLAIN SELECT * FROM secondhandcars WHERE km < 12000

On constate que la requête floue n'utilise pas l'index, au contraire de la requête non-floue.

Faites de même avec une requête floue retournant les voitures pas chères pour µ > 0.8 :

In [ ]:
%sql EXPLAIN SELECT 'TODO'

Puis à nouveau, quelle serait une requête non-floue équivalente, par exemple demandant un prix < 7000 :

In [ ]:
%sql EXPLAIN SELECT 'TODO'

Ici aussi, l'index est utilisé dans la requête non-floue mais pas la requête floue.

Essayons avec une requête conjonctive, celle avec la T-norme de la cellule #124. Ajoutez-lui `EXPLAIN` dans la cellule suivante pour voir la stratégie utilisée.

In [ ]:
%sql EXPLAIN SELECT 'TODO'

Comparez avec une requête non-floue qui cherche les voitures ayant un kilométrage inférieur à 5000 et un prix inférieur à 5000 et une année supérieure à 2009.

In [ ]:
%sql EXPLAIN SELECT 'TODO'

Le problème est que PostgreSQL ne peut pas analyser le comportement des fonctions floues à l'avance. Il n'y a que vous qui sachiez que telle fonction est linéaire par morceaux, par exemple décroissante entre 0 et une certaine valeur, etc.

### Requêtes flexibles dérivées

Heureusement, il y a un moyen d'utiliser l'index, à minima. C'est de construire une requête flexible dérivée. Pour rappel, la dérivation d’une requête flexible consiste à construire la requête « booléenne » retournant l’ensemble des tuples pouvant satisfaire la requête flexible, au mieux ceux d'une coupe alpha, au pire du support, puis à calculer le degré de satisfaction pour ces tuples uniquement. Cela se fait avec une double condition comme ceci :
```
SELECT ... WHERE conditions booléenne sur des coupes alpha ou les supports AND conditions sur le degré d'appartenance flou
```
Écrivez dans la cellule suivante la requête qui affiche le plan d’exécution d’une requête dérivée retournant les voitures de faible kilométrage pour µ > 0.8. La meilleure réponse est celle qui sélectionne sur une coupe alpha de la fonction floue à 0.8 ; une moins bonne réponse sélectionne tout le support.

In [ ]:
%sql EXPLAIN SELECT 'TODO'

Faites de même avec une requête floue retournant les voitures pas chères pour µ > 0.8 :

In [ ]:
%sql EXPLAIN SELECT 'TODO'

De même avec la requête dérivée qui affiche les voitures ayant à la fois un faible kimométrage, un prix faible et une année récente, à µ > 0.2.

In [ ]:
%%sql
EXPLAIN SELECT 'TODO'

En principe, les plans d'exécution montrent maintenant tous l'utilisation de l'index.

### Estimation de la cardinalité d'une fonction d'appartenance floue

On poursuit l'étude des fonctions d'appartenance floue et on se pose la question de la détermination rapide de leur cardinalité. Par exemple, combien de voitures satisfont cheap_price(prix) > 0.8 ?

Soit une fonction d'appartenance floue, $\mu_f(x)$ qui indique le degré d'appartenance de la valeur $x$ à $f$. On souhaite estimer le plus rapidement possible combien de n-uplets de la base de données ont la propriété $x$ qui satisfait $\mu_f(x) \ge \alpha$. Par exemple, combien de voitures ont un kilométrage modéré à plus de 0.8 : $\mu_{moderate\_mileage}(km) \ge 0.8$ ?

Un des moyens de le savoir est de parcourir la table et faire le calcul. Cela donne le résultat exact. C'est ce que fait la requête suivante.

In [ ]:
%sql SELECT COUNT(*) FROM secondhandcars WHERE moderate_mileage(km) >= 0.8

Cette requête effectue un parcours intégral des n-uplets de la table et calcule le degré d'appartenance pour chacun. Elle est équivalente au programme suivant, à compléter.

Ce programme commence par la définition en Python de la même fonction d'appartenance floue écrite précédemment en PL/SQL (il faut la traduire en Python en gardant les mêmes calculs). Puis il y a une boucle sur les données, l'évaluation de leur degré µ et le comptage.

In [ ]:
def getMuModerateMileage(km):
    if km is None: return 0.0
    # TODO all cases
    return 0.0

def getActualCardinalityModerateMileage(alpha):
    count = 0
    results = %sql SELECT * FROM secondhandcars
    for row in results:
        # TODO count rows that have getMuModerateMileage >= alpha
    return count

# actual count by the Python function
actual_count = getActualCardinalityModerateMileage(0.8)
print(f'actual_count = {actual_count}')

Le calcul précédent, SQL ou Python, serait très long sur une grande base de données, et encore plus long si on voulait connaître ces cardinalités sur tous les termes d'un vocabulaire flou (low_mileage, medium_mileage, etc). On se propose de programmer une technique d'estimation très rapide de la cardinalité, sans parcours des données, en utilisant les métadonnées.

Le principe est d'utiliser la fonction `getIntervalRelativeCardinalityV3` définie précédemment. On lui fournit un intervalle $[b1, b2]$ correspondant à la coupe alpha de la propriété floue au degré voulu. La difficulté est donc seulement de déterminer $b1$ et $b2$ pour `moderate_mileage` coupé à 0.8. Heureusement, la fonction d'appartenance floue est linéaire par morceaux, donc facilement inversible, sinon il faudrait résoudre l'équation $\mu(x)=0.8$ et trouver les deux $x$ qui la satisfont.

On commence par une fonction qui retourne les bornes $b1$ et $b2$ telles que $\alpha = µ_{moderate\_mileage}(b1)$ et $\alpha = µ_{moderate\_mileage}(b2)$ avec $b1 < b2$. La première est dans la partie gauche entre le support et le noyau, et l'autre est dans la partie droite. Il faut seulement inverser les équations.

In [ ]:
def getBoundsModerateMileageForAlpha(alpha):
    # parameter check
    if alpha <= 0.0 or alpha > 1.0: return None
    # when alpha == 1, return the core bounds
    if alpha == 1.0: return (15000, 50000)
    # solve b1,b2 so that getMuModerateMileage(b1) = getMuModerateMileage(b2) = alpha and b1 < b2
    b1 = 0    # TODO compute b1
    b2 = 1000 # TODO compute b2
    return b1, b2

# print results
b1, b2 = getBoundsModerateMileageForAlpha(0.8)
est_rel_card = getIntervalRelativeCardinalityV2('secondhandcars', 'km', b1, b2)
est_count = round(est_rel_card * tot_number_tuples)
rel_error = abs(est_count - actual_count) / actual_count * 100
print(f'est_count = {est_count}, actual_count={actual_count}, error = {rel_error:.1f}%')

Cette valeur estimée est, en principe, très proche de la véritable valeur. L'intérêt, c'est qu'elle est déterminée extrêmement rapidement en comparaison d'un parcours intégral des données. Dans la base des voitures, il y a très peu de données et les calculs sont très rapides, mais on peut arriver à plusieurs minutes voire bien davantage dans du Big Data.

Cette technique a été utilisée par l'équipe SHAMAN de l'IRISA, pour construire automatiquent et très rapidement des résumés linguistiques de grands jeux de données, c'est à dire générer des phrases décrivant les données à l'aide d'un vocabulaire flou. Par exemple, ici, on pourrait observer que « la plupart des voitures ont un prix faible et un kilométrage moyen ». C'est cela un résumé linguistique flou. Ces travaux ont été publiés, entre autres : G. Smits, P. Nerzic, O. Pivert, M.-J. Lesot. Efficient Generation of Reliable Estimated Linguistic Summaries. In Proc. of the 27th IEEE International Conference on Fuzzy Systems (Fuzz-IEEE'18), Rio de Janeiro, Brazil, 2018. *** Fuzz-IEEE 2018 Best Paper Award *** 

## Partie 3 : Une approche qualitative de gestion des préférences : « Skyline »

En considérant un ensemble de préférences définies sous la forme de fonctions croissantes (e.g. maximiser la puissance moteur, l’année, etc.) ou décroissantes (e.g. minimiser la consommation, le prix, etc.), l’approche « Skyline » consiste à déterminer l’ensemble des tuples non dominés par un autre tuple selon les préférences exprimées. La skyline donne une liste des n-uplets les plus intéressants, vis à vis d'un ensemble de critères fournis par l'utilisateur.

Pour commencer, rappelez la définition d’une relation de dominance entre deux tuples dans la cellule suivante.

<div class="alert alert-block alert-success"><span style='font-size:24px;'>&#9997;&nbsp;</span>
Un tuple T1 domine un autre tuple T2 si et seulement si TODO
</div>

Vous allez implémenter, dans la cellule suivante, l’algorithme de construction de la Skyline sur les tuples de la table SecondHandCars en cherchant à minimiser km et prix, et à maximiser l’année.

Le calcul de la skyline fait appel à la fonction `dominates(row1, row2)` qui applique la définition de la domination. On n'a pas cherché à rendre cette fonction générale, ce qui serait un peu compliqué, donc elle compare uniquement les trois attributs km, prix et année. Les paramètres sont des rangées retournées par la requête, donc ils portent directement les attributs `km`, `prix` et `annee` et on peut écrire `row1.prix`, `row2.km`, etc.

Ensuite, la fonction `getSkyLine()` consiste en une boucle sur la totalité des n-uplets, pour construire peu à peu la liste de ceux qui dominent tous les autres, sans qu'aucun d'entre eux ne domine un autre. Cette liste partielle de n-uplets peut changer à chaque n-uplet parcouru. A chaque tour de boucle sur un n-uplet, il y a un premier filtrage de cette liste pour éliminer ceux de ses n-uplets qui sont dominés par le n-uplet courant. Ensuite, le n-uplet courant n'est conservé que si aucun de ceux de la skyline ne le domine. La liste varie continuellement, en fonction des n-uplets rencontrés et à la fin, c'est la skyline du jeu de données.

Dans le programme ci-dessous, la fonction `getSkyLine()` retourne une paire, les noms des colonnes de la table et la liste des n-uplets. C'est pour permettre un affichage sous forme de table dans Jupyter.

In [ ]:
def dominates(row1, row2):
    "returns True if t1 dominates t2, else False"
    # TODO everything
    return False

def getSkyLine():
    "returns a pair headers (names of the columns) and skyline (rows from the table)"
    # future list of skyline tuples
    skyline = []
    # loop on every tuple in the table
    results = %sql SELECT * FROM secondhandcars
    for row in results:
        # TODO columns must not be null
        # TODO previous rows will stay in skyline if not dominated by the new one
        # TODO row can be added in skyline only if not dominated by any in the current skyline
    # final result
    return results.keys, skyline

# run the function
headers, skyline = getSkyLine()

# display results as a table
import tabulate
tabulate.tabulate(skyline, tablefmt='html', headers=headers)

Si tout va bien, vous obtiendrez 12 n-uplets. Vérifiez rapidement que chacun possède un attribut qui le rend meilleur vis à vis des critères choisis que les autres n-uplets : la voiture la moins chère, la plus récente, ayant le moins de kilomètres...

## Rendu du TP

Il vous suffit de déposer ce fichier .ipynb sur Moodle, dans l'espace de cours. Auparavant, il est demandé d'exécuter toutes les cellules puis d'enregistrer le cahier : menu Run, Run All Cells. Le fichier fait environ 5 à 6 Mo.